In [1]:
!pip install diffusers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 25.5 MB/s eta 0:00:00


In [2]:
import torch
import os
import cv2
from PIL import Image
import pandas as pd
import matplotlib.pyplot as plt

# Hugging face pipeline
from diffusers import StableDiffusionDepth2ImgPipeline


The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

2024-08-14 14:29:13.580982: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-08-14 14:29:13.581123: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-08-14 14:29:13.721667: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [3]:
pipe = StableDiffusionDepth2ImgPipeline.from_pretrained(
    "stabilityai/stable-diffusion-2-depth",
    torch_dtype=torch.float16)

pipe.to("cuda")

model_index.json:   0%|          | 0.00/545 [00:00<?, ?B/s]

Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

depth_estimator/config.json:   0%|          | 0.00/9.96k [00:00<?, ?B/s]

text_encoder/config.json:   0%|          | 0.00/732 [00:00<?, ?B/s]

tokenizer/merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

...

model.safetensors:   0%|          | 0.00/1.36G [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/3.46G [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

StableDiffusionDepth2ImgPipeline {
  "_class_name": "StableDiffusionDepth2ImgPipeline",
  "_diffusers_version": "0.30.0",
  "_name_or_path": "stabilityai/stable-diffusion-2-depth",
  "depth_estimator": [
    "transformers",
    "DPTForDepthEstimation"
  ],
  "feature_extractor": [
    "transformers",
    "DPTImageProcessor"
  ],
  "scheduler": [
    "diffusers",
    "PNDMScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "unet": [
    "diffusers",
    "UNet2DConditionModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}

In [4]:
class config:
    root = '/kaggle/input/government/政府單位'
    root2 = '/kaggle/input/company/公司'
train_data = pd.read_excel('/kaggle/input/government/dataset.xlsx')
train_data1 = pd.read_excel('/kaggle/input/company/dataset2.xlsx')

In [5]:
train_data1 

公司名稱 印章類型         影像路徑
0     群力投資    1    AS001.png
1     群力投資    2    AS002.png
2     運盈投資    1    AS003.png
3     運盈投資    2    AS004.png
4     運盈投資    3    AS005.png
..     ...  ...          ...
354   量石資本    1  PS354-2.png
355  還沒查清楚  NaN    PS355.png
356  還沒查清楚  NaN    PS356.png
357   紐約梅隆    1    QS357.png
358   天利基金    1    QS358.png

[359 rows x 3 columns]

# 政府機關

categorized_images = {}

for i in range(len(train_data)):
    category = train_data.所屬機關[i]
    image_name = train_data.影像路徑[i]
    image_path = os.path.join(config.root, category, image_name)
    
    try:
        img = Image.open(image_path).convert('RGB')

        if category not in categorized_images:
            categorized_images[category] = []
        # Store the image name and the image object as a tuple
        categorized_images[category].append((image_name, img))
    except Exception as e:
        print(f"Error loading image at {image_path}: {e}")

# Calculate the number of images in each category
image_counts = {}

for category, images in categorized_images.items():
    image_counts[category] = len(images)

# Print the number of images in each category
for category, count in image_counts.items():
    print(f"Category: {category}, Number of images: {count}")

# Specify the category you want to delete
category_to_delete = '台北地檢'

# Delete the specified category and its images
if category_to_delete in categorized_images:
    del categorized_images[category_to_delete]
    

category_to_delete = '台中地檢'

# Delete the specified category and its images
if category_to_delete in categorized_images:
    del categorized_images[category_to_delete]
    
    
category_to_delete = '士林地檢'

# Delete the specified category and its images
if category_to_delete in categorized_images:
    del categorized_images[category_to_delete]

# Directory for saving generated images
output_dir = "/kaggle/working/generated_images"
os.makedirs(output_dir, exist_ok=True)

prompt = "A similar photo to the original one"  # Adjust the prompt as needed
strength = 0.4  # Adjust the strength as needed

# Iterate over each category and generate images
for category, images in categorized_images.items():
    num_existing_images = len(images)
    num_images_to_generate = 80 - num_existing_images
    
    if num_images_to_generate > 0:
        gen_images = []
        gen_counter = {}  # Dictionary to track the number of times each image has been generated
        
        for i in range(num_images_to_generate):
            original_name, base_img = images[i % num_existing_images]  # Select a base image
            
            # Generate a new image using the pipeline
            with torch.no_grad():
                gen_img = pipe(prompt=prompt, image=base_img, strength=strength).images[0]
            
            # Track generation count for the original image
            if original_name not in gen_counter:
                gen_counter[original_name] = 0
            gen_counter[original_name] += 1
            
            # Create a new filename based on the original name and generation count
            filename = f"{os.path.splitext(original_name)[0]}_gen{gen_counter[original_name]:03d}.png"
            category_dir = os.path.join(output_dir, category)
            os.makedirs(category_dir, exist_ok=True)
            gen_img_path = os.path.join(category_dir, filename)
            gen_img.save(gen_img_path)
            gen_images.append((filename, gen_img))  # Store the new image with its name
        
        # Add generated images to the category in the dictionary
        categorized_images[category].extend(gen_images)
    
    # Notify when generation for the category is complete
    print(f"Generation complete for category: {category}")

# 公司

In [6]:
categorized_images = {}

for i in range(len(train_data1)):
    category = train_data1.公司名稱[i]
    image_name = train_data1.影像路徑[i]
    image_path = os.path.join(config.root2, category, image_name)
    
    try:
        img = Image.open(image_path).convert('RGB')

        if category not in categorized_images:
            categorized_images[category] = []
        # Store the image name and the image object as a tuple
        categorized_images[category].append((image_name, img))
    except Exception as e:
        print(f"Error loading image at {image_path}: {e}")

Error loading image at /kaggle/input/company/公司/永明投資/FS094.png: [Errno 2] No such file or directory: '/kaggle/input/company/公司/永明投資/FS094.png'
Error loading image at /kaggle/input/company/公司/士林地檢/HS126.png: [Errno 2] No such file or directory: '/kaggle/input/company/公司/士林地檢/HS126.png'
Error loading image at /kaggle/input/company/公司/還沒查清楚/JS239.png: [Errno 2] No such file or directory: '/kaggle/input/company/公司/還沒查清楚/JS239.png'
Error loading image at /kaggle/input/company/公司/還沒查清楚/NS291.png: [Errno 2] No such file or directory: '/kaggle/input/company/公司/還沒查清楚/NS291.png'


In [7]:
image_counts = {}

for category, images in categorized_images.items():
    image_counts[category] = len(images)

# Print the number of images in each category
for category, count in image_counts.items():
    print(f"Category: {category}, Number of images: {count}")

Category: 群力投資, Number of images: 15
Category: 運盈投資, Number of images: 13
Category: 羅豐投資, Number of images: 4
Category: 和遠國際公司, Number of images: 1
Category: 量石資本, Number of images: 13
Category: 第一證券, Number of images: 10
Category: 千興投資, Number of images: 10
Category: 還沒查清楚, Number of images: 34
Category: 忠訓國際, Number of images: 2
Category: 鴻錦投資, Number of images: 11
Category: 鼎智投資, Number of images: 10
Category: 寶利通科技, Number of images: 2
Category: 歐斯瑪再生能源科技, Number of images: 1
Category: 沐德投資, Number of images: 2
Category: 暘璨投資, Number of images: 8
Category: 立恒投資, Number of images: 4
Category: 長和資本, Number of images: 4
Category: 豐利投資, Number of images: 1
Category: 國喬投資開發, Number of images: 5
Category: 永鑫投資, Number of images: 11
Category: 永煌投資, Number of images: 2
Category: 明麗投資, Number of images: 3
Category: 好好證券, Number of images: 1
Category: 正華投資, Number of images: 3
Category: 圓方投資, Number of images: 6
Category: 沐笙資本, Number of images: 3
Category: 瑞泰投資, Number of images: 11
Categor

In [8]:
output_dir = "/kaggle/working/generated_images"
os.makedirs(output_dir, exist_ok=True)

In [9]:
prompt = "A similar photo to the original one"  # Adjust the prompt as needed
strength = 0.3  # Adjust the strength as needed

# Iterate over each category and generate images
for category, images in categorized_images.items():
    num_existing_images = len(images)
    num_images_to_generate = 10 - num_existing_images
    
    if num_images_to_generate > 0:
        gen_images = []
        gen_counter = {}  # Dictionary to track the number of times each image has been generated
        
        for i in range(num_images_to_generate):
            original_name, base_img = images[i % num_existing_images]  # Select a base image
            
            # Generate a new image using the pipeline
            with torch.no_grad():
                gen_img = pipe(prompt=prompt, image=base_img, strength=strength).images[0]
            
            # Track generation count for the original image
            if original_name not in gen_counter:
                gen_counter[original_name] = 0
            gen_counter[original_name] += 1
            
            # Create a new filename based on the original name and generation count
            filename = f"{os.path.splitext(original_name)[0]}_gen{gen_counter[original_name]:03d}.png"
            category_dir = os.path.join(output_dir, category)
            os.makedirs(category_dir, exist_ok=True)
            gen_img_path = os.path.join(category_dir, filename)
            gen_img.save(gen_img_path)
            gen_images.append((filename, gen_img))  # Store the new image with its name
        
        # Add generated images to the category in the dictionary
        categorized_images[category].extend(gen_images)
    
    # Notify when generation for the category is complete
    print(f"Generation complete for category: {category}")

Generation complete for category: 群力投資
Generation complete for category: 運盈投資


  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

...

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

Generation complete for category: 紐約梅隆
